In [202]:
from google.colab import drive
drive.mount('/content/gdrive')

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy import spatial
#import matplotlib.image as mpimg

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
plt.style.use('ggplot')

In [0]:
# Group markers
not_vulnerable_marker = 'circle'
vulnerable_marker = 'star-diamond'

# State colors
dark_green = px.colors.qualitative.D3[2]   # susceptible
dark_blue = px.colors.qualitative.D3[0]    # exposed
dark_red = px.colors.qualitative.D3[3]     # seriously-ill
dark_orange = px.colors.qualitative.D3[1]  # mildly-ill
dark_purple = px.colors.qualitative.G10[4] # asymptomatic
dark_gray = px.colors.qualitative.D3[7]    # recovered
dark_brown = px.colors.qualitative.Dark24[5]   # dead

# To plot with plotly, according to alphabetic orden of states
color_palette_no_dead = [dark_purple, dark_blue, dark_orange, dark_gray, dark_red, dark_green]
color_palette_dead = [dark_purple, dark_brown, dark_blue, dark_orange, dark_gray, dark_red, dark_green]

In [0]:
def initial_population_group_state_scene(
    population_number,
    vulnerable_number
):
    '''
    La funcion se puede mejorar en la incializacion del group list agregando una inicializacion aleatoria,
    (tal vez no sea muy importante) que respete las proporciones de poblacion en cada grupo,
    por el momento es una inicializacion secuencial
    '''
    population_group_list = [
        population_possible_groups[1] if i < vulnerable_number else population_possible_groups[0]
        for i in range(population_number)
    ]
    # Aqui se genera un solo incubador inicial, y todos los demas susceptibles
    population_state_list = [
        population_possible_states[1] if i == np.floor(population_number/2) else population_possible_states[0]
        for i in range(population_number)
    ]
    
    return population_group_list, population_state_list

In [0]:
def plot_states_evolution_plotly(dataframe):
    # Get number of steps in dataframe:
    number_of_steps_dataframe = dataframe.tail(1)['step'].to_numpy()[0]
    days_array = np.arange(number_of_steps_dataframe + 1)
    # Tabla cruzada de estados y pasos (dias)
    time_series_agents = pd.crosstab(dataframe['state'], dataframe['step']).fillna(0) * 100 / population_number # To get a percent of population
    if len(time_series_agents.index) > 6:
        color_palette_graph = color_palette_dead
    elif len(time_series_agents.index) == 6:
        color_palette_graph = color_palette_no_dead
    # Plot
    fig = go.Figure()
    for (series, category, color) in zip(time_series_agents.values, time_series_agents.index, color_palette_graph):
        # Add each trace
        fig.add_trace(go.Scatter(x=days_array, y=series, mode='lines+markers', name=category, line = dict(color=color, width=4 )))
    # Format graph
    fig.update_layout(autosize=False, width=900, height=600,
                      title='Estados de población vs días Simulación agentes N={}, L={}, V_max={}'.format(population_number, horizontal_length, maximum_speed),
                      xaxis_title='Días',
                      yaxis_title='Porcentaje población')
    fig.show()

In [0]:
###################################################
# PARAMETROS SIMULACION                           #
###################################################

#--------------------#
# Población          #
#--------------------#
# Dimension del espacio:
dim = 2
# Numero de agentes:
population_number = 100
# Tamaño de la cuadricula:
horizontal_length = 80
vertical_length = 80
# Porcentaje población vulnerable:
vulnerable_population_pct = 0.2
# Cantidad de población vulnerable
vulnerable_number = np.ceil(population_number * vulnerable_population_pct)

#---------------------#
# Radios de contagio  #
#---------------------#
# Radio de contagio para enfermos 
contagion_radius_sick = 2
# Radio de distancia social a supuestamente aliviados
social_distancing_radius_to_apparently_healthy = 1
# Radio de distancia social a supuestamente enfermos
social_distancing_radius_to_apparently_sick = 3

#----------------------------------#
# Probabilidades de transicion     #
#----------------------------------#
# Probability of reinfection reduction factor: (Proporcion que se reduce la probabilidad de ser reinfectado)
factor_reduccion_probabilidad_de_reinfecccion = 0.25
# --------1. No Vulnerables----------------#
# De Susceptibles a expuestos: probabilidad promedio (En una distribucion normal de probabilidades)
Probabilidad_transicion_susceptible_a_expuesto_NV_Ref = 0.7 # Valor de referencia promedio de probabilidades de contagiarse para este grupo
# probabilidades de transicion desde incubacion
Probabilidad_transicion_expuesto_a_seriously_NV = 0.05
Probabilidad_transicion_expuesto_a_mildly_NV = 0.55
Probabilidad_transicion_expuesto_a_asymptomatic_NV = 0.4
# Probabilidades desde asintomatico
Probabilidad_transicion_stay_asymptomatic_NV = 0.5
Probabilidad_transicion_asymptomatic_a_seriously_NV = 0.15
Probabilidad_transicion_asymptomatic_a_mildly_NV = 0.8
Probabilidad_transicion_asymptomatic_a_susceptible_NV = 0.0
# probabilidades de transicion desde enfermos
Probabilidad_transicion_seriously_a_recovered_NV = 0.95 # Los demas van a muertos
Probabilidad_transicion_mildly_a_recovered_NV = 0.98 # Los demas van para seriously
# Desde recuperados (transiciones espontaneas al cabo del maximo dias sin transicion)
Probabilidad_transicion_stay_recovered_NV = 0.9 # Quedarse en estado recuperado
Probabilidad_transicion_recovered_a_exposed_NV = 0.06 # Pasar a incubador
Probabilidad_transicion_recovered_a_mildly_NV = 0.03 # Pasar a sintomas leves
Probabilidad_transicion_recovered_a_seriously_NV = 0.01 # Pasar a sintomas graves

# ---------2. Vulnerables----------------------
# De Susceptibles a expuestos: probabilidad promedio (En una distribucion normal de probabilidades)
Probabilidad_transicion_susceptible_a_expuesto_V_Ref = 0.85
# probabilidades de transicion desde incubacion
Probabilidad_transicion_expuesto_a_seriously_V = 0.15
Probabilidad_transicion_expuesto_a_mildly_V = 0.6
Probabilidad_transicion_expuesto_a_asymptomatic_V = 0.25
# Probabilidades desde asintomatico
Probabilidad_transicion_stay_asymptomatic_V = 0.04
Probabilidad_transicion_asymptomatic_a_seriously_V = 0.18
Probabilidad_transicion_asymptomatic_a_mildly_V = 0.78
Probabilidad_transicion_asymptomatic_a_susceptible_V = 0
# probabilidades de transicion desde enfermos
# Solo hay dos resultados finales: recovered o dead, entonces la transicion es binaria solamente
Probabilidad_transicion_seriously_a_recovered_V = 0.9 # Los demas van a muertos
Probabilidad_transicion_mildly_a_recovered_V = 0.95 # Los demas van para seriously
# Desde recuperados (transiciones espontaneas al cabo del maximo dias sin transicion)
Probabilidad_transicion_stay_recovered_V = 0.85 # Quedarse en estado recuperado
Probabilidad_transicion_recovered_a_exposed_V = 0.08 # Pasar a incubador
Probabilidad_transicion_recovered_a_mildly_V = 0.05 # Pasar a sintomas leves
Probabilidad_transicion_recovered_a_seriously_V = 0.02 # Pasar a sintomas graves

#---------------------------------#
# Probabilidades de diagnosticos  #
#---------------------------------#
# Asintomatico
probabilidad_diagnostico_por_dia_asintomatico = 0.02
# Leve
probabilidad_diagnostico_por_dia_leve = 0.1
# Grave
probabilidad_diagnostico_por_dia_grave = 0.8

#---------------------------#
# Parametros velocidad      #
#---------------------------#
# Rapidez maxima agentes:
maximum_speed = 5
# Speed reduction fators on transitions (In the interval [0,1], where 0 is complete reduction and 1 is no reduction)
speed_reduction_asymptomatic = 1 
speed_reduction_mild_sick = 0.2
speed_reduction_serious_sick = 0.02
speed_reduction_diagnosed = 0.01

#----------------------#
# Days parameters      #
#----------------------#
#----------Incubation------#
# Possible amount of days of incubation:
minimum_incubation_days = 2
maximum_incubation_days = 14
#---------Asymptomatic-----#
# Possible amount of asymptomatic days
minimum_asymptomatic_days = 8
maximum_asymptomatic_days = 14
# Para partir el intervalo de dias en dos tercios segun grupo vulnerable o no:
two_thirds_asymptomatic_split_days = int( (maximum_asymptomatic_days - minimum_asymptomatic_days)/3 )
#----------Sick-----------#
# Possible amount of sick days
minimum_sick_days = 8
maximum_sick_days = 14
# Para partir el intervalo de dias en dos tercios segun grupo vulnerable o no
two_thirds_sick_split_days = int( (maximum_sick_days - minimum_sick_days)/3 )
#-----------Recovered-----#
# Dias que un recuperado puede contagiar
min_days_recovered_can_spread = 3
max_days_recovered_can_spread = 6
# Dias para que un recuperado haga alguna transicion a quedarse recuperado, leve, grave, o expuesto
max_days_recovered_can_transition = 14

#----------------------------#
# Graphical parameters       #
#----------------------------#
# Parametros graficos agentes
agent_size = 10
agent_opacity = 1.0
agent_marker_line_width = 2

#---------------------------------------#
# Diccionarios agentes y transiciones   #
#---------------------------------------#
population_possible_states = [
    'susceptible',
    'exposed',
    'seriously-ill',
    'mildly-ill',
    'asymptomatic',
    'recovered',
    'dead'
]

# Estados que pueden contagiar
population_can_spread_states = ['exposed', 'seriously-ill', 'mildly-ill', 'asymptomatic', 'recovered'] # Recovered solo por unos dias, los demas pueden contagiar todo el tiempo
# Estados contagiables:
population_infectable_states = ['susceptible', 'recovered']
# Estados aparentemente sanos
population_apparently_healthy_states = ['susceptible', 'exposed', 'asymptomatic', 'recovered']
# Estados aparentemente enfermos
population_apparently_sick_states = ['seriously-ill', 'mildly-ill']
# Estados realmente enfermos
population_actually_sick_states = ['seriously-ill', 'mildly-ill','asymptomatic']

# Diccionario factores de reduccion velocidad
speed_reduction_factors = {
    'asymptomatic' : speed_reduction_asymptomatic,
    'seriously-ill': speed_reduction_serious_sick,
    'mildly-ill' : speed_reduction_mild_sick
}

# Diccionario probabilidades de diganostico por dia
diagnostics_probabilities_per_day = {
    'asymptomatic' : probabilidad_diagnostico_por_dia_asintomatico,
    'mildly-ill' : probabilidad_diagnostico_por_dia_leve,
    'seriously-ill' : probabilidad_diagnostico_por_dia_grave
}

# Diccionario probabilidades transiciones de estados
population_possible_transitions = {
    'not-vulnerable': {
        'exposed': {
            'seriously-ill': Probabilidad_transicion_expuesto_a_seriously_NV,
            'mildly-ill' : Probabilidad_transicion_expuesto_a_mildly_NV,
            'asymptomatic' : Probabilidad_transicion_expuesto_a_asymptomatic_NV
            },
        'seriously-ill': {
            'recovered' : Probabilidad_transicion_seriously_a_recovered_NV,
            'dead' : 1 - Probabilidad_transicion_seriously_a_recovered_NV
        },
        'mildly-ill' : {
            'recovered' : Probabilidad_transicion_mildly_a_recovered_NV,
            'seriously-ill' : 1 - Probabilidad_transicion_mildly_a_recovered_NV
        },
        'asymptomatic' : {
            'asymptomatic' : Probabilidad_transicion_stay_asymptomatic_NV,
            'seriously-ill' : Probabilidad_transicion_asymptomatic_a_seriously_NV,
            'mildly-ill' : Probabilidad_transicion_asymptomatic_a_mildly_NV,
            'susceptible' : Probabilidad_transicion_asymptomatic_a_susceptible_NV
        },
        'recovered': {
            'recovered' : Probabilidad_transicion_stay_recovered_NV,
            'exposed' : Probabilidad_transicion_recovered_a_exposed_NV,
            'mildly-ill' : Probabilidad_transicion_recovered_a_mildly_NV,
            'seriously-ill' : Probabilidad_transicion_recovered_a_seriously_NV
        }
    },
    'vulnerable': {
        'exposed': {
            'seriously-ill': Probabilidad_transicion_expuesto_a_seriously_V,
            'mildly-ill' : Probabilidad_transicion_expuesto_a_mildly_V,
            'asymptomatic' : Probabilidad_transicion_expuesto_a_asymptomatic_V
            },
        'seriously-ill': {
            'recovered' : Probabilidad_transicion_seriously_a_recovered_V,
            'dead' : 1 - Probabilidad_transicion_seriously_a_recovered_V
        },
        'mildly-ill' : {
            'recovered' : Probabilidad_transicion_mildly_a_recovered_V,
            'seriously-ill' : 1 - Probabilidad_transicion_mildly_a_recovered_V
        },
        'asymptomatic' : {
            'asymptomatic' : Probabilidad_transicion_stay_asymptomatic_V,
            'seriously-ill' : Probabilidad_transicion_asymptomatic_a_seriously_V,
            'mildly-ill' : Probabilidad_transicion_asymptomatic_a_mildly_V,
            'susceptible' : Probabilidad_transicion_asymptomatic_a_susceptible_V
        },
        'recovered': {
            'recovered' : Probabilidad_transicion_stay_recovered_V,
            'exposed' : Probabilidad_transicion_recovered_a_exposed_V,
            'mildly-ill' : Probabilidad_transicion_recovered_a_mildly_V,
            'seriously-ill' : Probabilidad_transicion_recovered_a_seriously_V
        }
    }
    
}

population_possible_groups = ['not-vulnerable', 'vulnerable']

population_possible_groups_markers = {
    'not-vulnerable': not_vulnerable_marker,
    'vulnerable': vulnerable_marker
}

population_color_dicts = {
    'not-vulnerable': {
        'susceptible': dict(
            color=dark_green,
            size=agent_size,
            opacity=agent_opacity
        ),
        'exposed': dict(
            color=dark_blue,
            size=agent_size,
            opacity=agent_opacity
        ),
        'seriously-ill': dict(
            color=dark_red,
            size=agent_size,
            opacity=agent_opacity
        ),
        'mildly-ill': dict(
            color=dark_orange,
            size=agent_size,
            opacity=agent_opacity
        ),
        'asymptomatic': dict(
            color=dark_purple,
            size=agent_size,
            opacity=agent_opacity
        ),
        'recovered': dict(
            color=dark_gray,
            size=agent_size,
            opacity=agent_opacity
        ),
        'dead': dict(
            color=dark_brown,
            size=agent_size,
            opacity=agent_opacity
        )
    },
    'vulnerable': {
        'susceptible': dict(
            color=dark_green,
            size=agent_size,
            opacity=agent_opacity
        ),
        'exposed': dict(
            color=dark_blue,
            size=agent_size,
            opacity=agent_opacity
        ),
        'seriously-ill': dict(
            color=dark_red,
            size=agent_size,
            opacity=agent_opacity
        ),
        'mildly-ill': dict(
            color=dark_orange,
            size=agent_size,
            opacity=agent_opacity
        ),
        'asymptomatic': dict(
            color=dark_purple,
            size=agent_size,
            opacity=agent_opacity
        ),
        'recovered': dict(
            color=dark_gray,
            size=agent_size,
            opacity=agent_opacity
        ),
        'dead': dict(
            color=dark_brown,
            size=agent_size,
            opacity=agent_opacity
        )
    }
}


#===========================================================================

class Agent():
    """
    
    """
    
    def __init__(
        self,
        agent: int,
        x: float,
        y: float,
        vmax: float,
        group: str,
        state: str,
        #contagion_radius: float,
        #social_distancing_radius: float,
        diagnosed: bool=False
    ):
        """
    
        """
        # Define agent label (Identifier number)
        self.agent = agent
        
        # Define position
        self.x = x
        self.y = y
        
        # Define initial velocity in each component in the interval[-vmax,vmax]
        self.vx, self.vy = 2. * vmax * np.random.random_sample(dim) - vmax
        
        # Initialize group, state, and diagnosed state
        self.group = group
        
        self.state = state
        
        self.diagnosed = diagnosed
        '''
        # Inicializamos radio de contagio
        if self.state == 'susceptible' or self.state == 'recovered':
            self.contagion_radius = contagion_radius_healthy
    
        if self.state == 'exposed' or self.state == 'seriously-ill' or self.state == 'mildly-ill' or self.state == 'asymptomatic':
            self.contagion_radius = contagion_radius_sick

        # Inicializamos radio de distancia social
        self.social_distancing_radius = social_distancing_radius_population
        '''
        # Inicializamos probabilidad de pasar a expuesto como una distribucion normal alrededor de los valores de referencia fijados como parametros
        if self.group == 'not-vulnerable':
            self.probability_of_becoming_exposed = np.random.normal(loc = Probabilidad_transicion_susceptible_a_expuesto_NV_Ref, scale = 0.1)
        if self.group == 'vulnerable':
            self.probability_of_becoming_exposed = np.random.normal(loc = Probabilidad_transicion_susceptible_a_expuesto_V_Ref, scale = 0.07)

        # Incializamos contador de dias de incubacion
        #self.days_as_exposed_agent_counter = 0
        # Maximo de dias de incubacion del agente
        self.max_days_of_incubation_agent = np.random.randint(low = minimum_incubation_days, high = maximum_incubation_days + 1)

        # Inicializamos contador dias asintomatico 
        #self.days_as_asymptomatic_agent_counter = 0
        # Maximo dias asintomatico del agente
        if self.group == 'not-vulnerable':
            self.max_days_as_asymptomatic_agent = np.random.randint(low = minimum_asymptomatic_days, high = (maximum_asymptomatic_days - two_thirds_asymptomatic_split_days + 1) )
        if self.group == 'vulnerable':
            self.max_days_as_asymptomatic_agent = np.random.randint(low = (minimum_asymptomatic_days + two_thirds_asymptomatic_split_days), high = maximum_asymptomatic_days + 1  )

        # Incializamos contmador de dias de enfermo:
        #self.days_as_sick_agent_counter = 0
        # Maximo de dias de enfermo del agente:
        if self.group == 'not-vulnerable':
            self.max_days_as_sick_agent = np.random.randint(low = minimum_sick_days, high = (maximum_sick_days - two_thirds_sick_split_days + 1) )
        if self.group == 'vulnerable':
            self.max_days_as_sick_agent = np.random.randint(low = (minimum_sick_days + two_thirds_sick_split_days), high = maximum_sick_days + 1 )

        # Estado del agente que lo infectó
        self.infected_by_state = None
        
        # Estado del agente que lo infectó
        self.infected_by_agent = None

        # Si puede contagiar o no
        if self.state == 'susceptible':
            self.agent_can_spread_bool = False
        else:
            self.agent_can_spread_bool = True

        self.states_agent_days_dictionary = {
            'exposed' : {
                'counter' : 0,
                'max_days' : self.max_days_of_incubation_agent
            },
            'asymptomatic' : {
                'counter' : 0,
                'max_days' : self.max_days_as_asymptomatic_agent
            },
            'mildly-ill' : {
                'counter' : 0,
                'max_days' : self.max_days_as_sick_agent
            },
            'seriously-ill' : {
                'counter' : 0,
                'max_days' : self.max_days_as_sick_agent
            },
            'recovered' : {
                'counter' : 0,
                'max_days' : max_days_recovered_can_transition,
                'max_days_spread' : np.random.randint(low=min_days_recovered_can_spread, high = max_days_recovered_can_spread + 1)
            },
            'dead' : {
                'counter' : 0
            }
        }


class Population():
    """
    
    """
    def __init__(
        self,
        population_number: int,
        vulnerable_number: int,
        population_group_list: list,
        population_state_list: list,
        horizontal_length: float,
        vertical_length: float,
        maximum_speed: float
    ):
        """
    
        """
        # Initialize step
        self.step = 0
        self.dt = 1
        
        # Initialize population number
        self.initial_population_number = population_number
        self.population_numbers = [self.initial_population_number] # Is this to keep track of this number?
            
        
        # Initialize vulnerable people number
        self.vulnerable_number = vulnerable_number
        
        # Initialize maximum free random speed
        #self.maximum_free_random_speed = maximum_free_random_speed
        
        # Initialize horizontal and vertical length
        self.xmax = horizontal_length/2
        self.xmin = -horizontal_length/2
        self.ymax = vertical_length/2
        self.ymin = -vertical_length/2
    
        # Create list of agents
        self.population = [
            Agent(
                # Define label
                agent=i,
                
                # Define positions as random
                x=(self.xmax - self.xmin) * np.random.random_sample() + self.xmin, # could be: x=horizontal_length * np.random.random_sample() + self.xmin,
                y=(self.ymax - self.ymin) * np.random.random_sample() + self.ymin, # could be: x=vertical_length * np.random.random_sample() + self.xmin,
                
                # Set up maximum speed
                vmax=maximum_speed,
                
                # Define population group
                group=population_group_list[i],
                
                # Define state
                state=population_state_list[i]
                
            ) for i in range(self.initial_population_number)
        ]

        # Initialize Pandas DataFrame
        keys = list(self.population[0].__dict__.keys())[:-1] # Avoid writing states_days_dictionary
        keys.append('step')
        self.agents_info_df = pd.DataFrame(columns = keys)
        
        # Populate DataFrame
        self.populate_df(self.step)

        # Spatial tree to calculate distances fastly
        self.spatial_tree = spatial.KDTree( np.c_[[self.population[i].x for i in range(population_number) ], [self.population[i].y for i in range(population_number) ]] )

    def evolve_population(self):
        # Cycle runs along all agents in current population number

        # First make all state transitions
        for i in range(self.population_numbers[-1]):
            alert = False
            if not alert:
                self.state_transitions(i, from_sick_to_healthy=False)

        # Hacemos los diagnosticos
        self.diagnostics_function()

        # Hacemos que los agentes tomen decision de alejarse
        self.social_avoidance_function()

        # Then move population        
        for i in range(self.population_numbers[-1]):
            alert = False
            # Include function calculating ALL the neighboors
            # inside the radius of each state, and then chante ALERT if
            # any neighboor fulfills conditions for being alert
            # Remember that:
            # 'seriously-ill' has one radius if diagnosed and other radius if not diagnosed
            # 'mildly-ill' has one radius if diagnosed and other radius if not diagnosed
            # 'asymptomatic' (but diagnosed) have one radius too
            
            if not alert:
                self.free_physical_movement(i)
        
        # Recalcular el arbol de distancias
        self.spatial_tree = spatial.KDTree( np.c_[[self.population[i].x for i in range(population_number) ], [self.population[i].y for i in range(population_number) ]] )

        # Evolve step
        self.step = self.step + self.dt
        
        # TODO
        # Include function calculating population STATES
        # Should we use the label 'Death' in the state or simply remove the agent?
        # If infected, update 'infected_by' attribute as an array: [agent_i, agent_j, agent_k, ...]
        
        # Include function adding the new population number
        
        # Populate DataFrame
        self.populate_df(self.step)
        
        # Update xmin, xmax, ymin, ymax
        self.xmin = self.agents_info_df['x'].min()
        self.xmax = self.agents_info_df['x'].max()
        self.ymin = self.agents_info_df['y'].min()
        self.ymax = self.agents_info_df['y'].max()

    def change_direction_of_agent(self, agent_a_index: int, agent_b_index: int):
        '''
        Cambia la velocidad de los agentes si se encuentran dentro del radio de distancia social de sanos o de enfermos
        '''
        speed_magnitude = np.sqrt(self.population[agent_a_index].vx**2 + self.population[agent_a_index].vy**2)
        # Vector de direccion opuesta entre agentes:
        opposite_direction_vector = np.array([ self.population[agent_a_index].x - self.population[agent_b_index].x, self.population[agent_a_index].y - self.population[agent_b_index].y ])
        norm_of_vector = np.linalg.norm(opposite_direction_vector)
        unitary_opposite_direction_vector = opposite_direction_vector/norm_of_vector
        self.population[agent_a_index].vx = speed_magnitude*unitary_opposite_direction_vector[0] 
        self.population[agent_a_index].vy = speed_magnitude*unitary_opposite_direction_vector[1] 

    '''
    def exposed_transition_function(self, agent_index: int):
        random_number = np.random.random()
        # A seriously
        if random_number < population_possible_transitions[self.population[agent_index].group][self.population[agent_index].state]['seriously-ill']:
            self.population[agent_index].state = 'seriously-ill'
        # A Asymptomatic
        elif random_number > (1-population_possible_transitions[self.population[agent_index].group][self.population[agent_index].state]['asymptomatic']):
            self.population[agent_index].state = 'asymptomatic'
        else: 
            self.population[agent_index].state = 'mildly-ill'
        
        # Change the speed of movement according to the appropriate factor
        self.population[agent_index].vx *= speed_reduction_factors[self.population[agent_index].state]
        self.population[agent_index].vy *= speed_reduction_factors[self.population[agent_index].state]
        # Reset incubation days for further possible infection
        # self.population[agent_index].days_as_exposed_agent = 0
    '''

    def generalized_state_transition_function_non_susceptibles(self, agent_index: int):
        # Change state according to probability. This line finds the interval of the cumulative sums of probabilities that corresponds
        # to the state to transition
        self.population[agent_index].state = list(population_possible_transitions[self.population[agent_index].group][self.population[agent_index].state].keys()) [len(
            population_possible_transitions[self.population[agent_index].group][self.population[agent_index].state]) - sum(
                 np.random.random() <= np.cumsum(list(population_possible_transitions[self.population[agent_index].group][self.population[agent_index].state].values())) ) ]
        
        # Change the speed of movement according to the appropriate factor
        if self.population[agent_index].state in population_actually_sick_states:
            self.population[agent_index].vx *= speed_reduction_factors[self.population[agent_index].state]
            self.population[agent_index].vy *= speed_reduction_factors[self.population[agent_index].state]
        
    def diagnostics_function(self):
        '''
        Esta funcion realiza los diagnosticos para cada agente
        '''
        for agent_index in range(self.population_numbers[-1]):
            # El diagnostico es solo para los realmente enfermos: asintomaticos, leves o graves diagnostics_probabilities_per_day
            if self.population[agent_index].state in population_actually_sick_states and not self.population[agent_index].diagnosed:
                self.population[agent_index].diagnosed = np.random.random() < diagnostics_probabilities_per_day[self.population[agent_index].state]
                if self.population[agent_index].diagnosed:
                    self.population[agent_index].vx *= speed_reduction_diagnosed
                    self.population[agent_index].vy *= speed_reduction_diagnosed

    def social_avoidance_function(self):
        '''
        Esta funcion modifica las velocidades de los agentes con base en la cercanía de enfermos u otras personas
        '''
        for agent_index in range(self.population_numbers[-1]):
            # Check distance to closest neighbor to decide movement
            # Va a devolver dos vecinos pues el mas cercano siempre es el mismo agente
            closest_neighbor = self.spatial_tree.query([self.population[agent_index].x, self.population[agent_index].y], k = 2 )
            if closest_neighbor[0][1] < social_distancing_radius_to_apparently_healthy and self.population[closest_neighbor[1][1]].state in population_apparently_healthy_states:
                self.change_direction_of_agent(agent_index, closest_neighbor[1][1])

            # Ahora Chequeamos si cumple el radio de aparentemente enfermos y si es  enfermo
            elif closest_neighbor[0][1] < social_distancing_radius_to_apparently_sick and self.population[closest_neighbor[1][1]].state in population_apparently_sick_states: # Distance to closest neighbor
                self.change_direction_of_agent(agent_index, closest_neighbor[1][1])
        
    def state_transitions(self, agent_index: int, from_sick_to_healthy: bool):
        '''
        Esta funcion calcula las transiciones de estados: de expuestos a enfermos, de enfermos a recuperados o muertos
        '''
        # This option calculates neighbors within the contagion radius only if the current agent is sick
        if from_sick_to_healthy:
            # finding if individual will spread disease to others because of distance
            if self.population[agent_index].agent_can_spread_bool:
                # First, find neighbors within contagion radius
                neighbors = self.spatial_tree.query_ball_point([self.population[agent_index].x, self.population[agent_index].y], r = contagion_radius_sick)
                if len(neighbors) > 1:
                    # Eliminate current agent from list of neighbors
                    neighbors.remove(agent_index)
                    # change status of those within radius
                    for case_to_change_status in (neighbors):
                        if self.population[case_to_change_status].state in population_infectable_states:
                            self.population[case_to_change_status].state = 'exposed' 
                            self.population[case_to_change_status].infected_by_state = self.population[agent_index].state
                            self.population[case_to_change_status].infected_by_agent = agent_index
        
        # This option calculates neighbors within the contagoin radius only if the current agent is infectable
        else:
            # finding if healthy agent has sick neighbors within contagion radius
            if self.population[agent_index].state in population_infectable_states:
                # First, find neighbors within contagion radius
                neighbors = self.spatial_tree.query_ball_point([self.population[agent_index].x, self.population[agent_index].y], r = contagion_radius_sick)
                if len(neighbors) > 1:
                    # Eliminate current agent from list of neighbors
                    neighbors.remove(agent_index)
                    # change status of agent if at least one neighbor is sick and based on probability:
                    for neighbor in (neighbors):
                        if self.population[neighbor].agent_can_spread_bool:
                            if np.random.random() < self.population[agent_index].probability_of_becoming_exposed:
                                if self.population[agent_index].state == 'recovered':
                                    self.population[agent_index].states_agent_days_dictionary[self.population[agent_index].state]['counter'] = 0
                                self.population[agent_index].state = 'exposed' 
                                self.population[agent_index].infected_by_state = self.population[neighbor].state
                                self.population[agent_index].infected_by_agent = neighbor
                                self.population[agent_index].agent_can_spread_bool = True
                                break

        # State transitions for non susceptibles nor dead:
        if self.population[agent_index].state not in ['susceptible', 'dead']:
            # Check if counter days is equal to max days according to state
            if self.population[agent_index].states_agent_days_dictionary[
                                        self.population[agent_index].state]['counter'] == self.population[
                                                                agent_index].states_agent_days_dictionary[self.population[agent_index].state]['max_days']:
                # Store former state to avoid reducing probability many times for recovered
                former_state = self.population[agent_index].state
                # Reset counter for other transition to the same state
                self.population[agent_index].states_agent_days_dictionary[self.population[agent_index].state]['counter'] = 0
                # Call transition function (This function changes the current agent state and its speed)
                self.generalized_state_transition_function_non_susceptibles(agent_index)
                # Update can spread status if now can spread:
                if self.population[agent_index].state in population_actually_sick_states:
                    self.population[agent_index].agent_can_spread_bool = True
                # Recover speed if got to state recovered:
                if self.population[agent_index].state == 'recovered' and former_state != 'recovered':
                    # Give the agent a new speed
                    self.population[agent_index].vx, self.population[agent_index].vy = 2. * maximum_speed * np.random.random_sample(dim) - maximum_speed
                    # Update probability of becoming exposed:
                    self.population[agent_index].probability_of_becoming_exposed *= factor_reduccion_probabilidad_de_reinfecccion
                    # Remove diagnosed tag
                    self.population[agent_index].diagnosed = False
                # If dead, change speed to zero
                elif self.population[agent_index].state == 'dead':
                    self.population[agent_index].vx, self.population[agent_index].vy = 0, 0
            # If not increase counter of days of state
            else:
                self.population[agent_index].states_agent_days_dictionary[self.population[agent_index].state]['counter'] += 1
            # Stop spreading for recovered after max recovered can spread days
            if self.population[agent_index].state == 'recovered' and  self.population[agent_index].states_agent_days_dictionary[
                                        self.population[agent_index].state]['counter'] == self.population[
                                                                agent_index].states_agent_days_dictionary[self.population[agent_index].state]['max_days_spread']:
                self.population[agent_index].agent_can_spread_bool = False

        '''
        # Transicion a enfermos (A condicion de haber pasado los dias de incubacion)
        if self.population[agent_index].state == 'exposed' and self.population[agent_index].days_as_exposed_agent_counter == max_days_of_incubation_agent:
            # Call the exposed transition function
            self.exposed_transition_function(agent_index)

        # Transicion a recuperados o muertos
        if self.population[agent_index].state in population_actually_sick_states and self.population[agent_index].days_as_sick_agent == days_of_sickness:
            # Re-adjust speed by appropriate factor
            self.population[agent_index].vx /= speed_reduction_factors[self.population[agent_index].state]
            self.population[agent_index].vy /= speed_reduction_factors[self.population[agent_index].state]
            # Transition
            random_number = np.random.random()
            if random_number < population_possible_transitions[self.population[agent_index].group][self.population[agent_index].state]['recovered']:
                self.population[agent_index].state = 'recovered'
            else:
                self.population[agent_index].state = 'dead'
                self.population[agent_index].vx = 0
                self.population[agent_index].vy = 0
        

        # Chequear si es expuesto para aumentar sus dias de incubacion
        if self.population[agent_index].state == 'exposed':
            self.population[agent_index].days_as_exposed_agent += 1
        
        # Chequear si es enfermo para aumentar sus dias de enfermo
        if self.population[agent_index].state in population_actually_sick_states:
            self.population[agent_index].days_as_sick_agent += 1
        '''
            
    def free_physical_movement(self, agent_index: int):
            
        # Evolve position
        self.population[agent_index].x = self.population[agent_index].x + self.population[agent_index].vx * self.dt
        self.population[agent_index].y = self.population[agent_index].y + self.population[agent_index].vy * self.dt
    
        # Bouncing from the walls:
        # Hitting upper or lower wall 
        if self.population[agent_index].x > self.xmax or self.population[agent_index].x < self.xmin:
            self.population[agent_index].x = self.population[agent_index].x - self.population[agent_index].vx * self.dt
            self.population[agent_index].vx = -self.population[agent_index].vx
        
        # Hitting left or right wall
        if self.population[agent_index].y > self.ymax or self.population[agent_index].y < self.ymin:
            self.population[agent_index].y = self.population[agent_index].y - self.population[agent_index].vy * self.dt
            self.population[agent_index].vy = -self.population[agent_index].vy
        
        
    def alert_physical_movement(self, agent_index: int):
        #TODO
        # Include to move aside from ill people
        return None

    
    def populate_df(self, step: int):
        # Cycle runs along all agents in current population number
        for i in range(self.population_numbers[-1]):
            # agent_dict = self.population[i].__dict__
            agent_dict = {k:v for (k,v) in self.population[i].__dict__.items() if k not in ['states_agent_days_dictionary']}
            agent_dict['step'] = step
            
            self.agents_info_df = self.agents_info_df.append(
                agent_dict,
                ignore_index=True
            )


    def go_agent_scatter(self, agent_dict: dict):
        agent_label = agent_dict['agent']
        x = agent_dict['x']
        y = agent_dict['y']
        vx = agent_dict['vx']
        vy = agent_dict['vy']
        group = agent_dict['group']
        state = agent_dict['state']
        diagnosed = agent_dict['diagnosed']
        infected_by = agent_dict['infected_by_state']
        
        template = (
            f'<b>Agent</b>: {agent_label}'
            '<br>'
            f'<b>Position</b>: ({x:.2f}, {y:.2f})'
            '<br>'
            f'<b>Velocity</b>: ({vx:.2f}, {vy:.2f})'
            '<br>'
            f'<b>Group</b>: {group}'
            '<br>'
            f'<b>State</b>: {state}'
            '<br>'
            f'<b>Diagnosed</b>: {diagnosed}'
            '<br>'
            f'<b>Infected by</b>: {infected_by}'
        )
        
        return  go.Scatter(
            x=[x],
            y=[y],
            mode='markers',
            marker_line_width=agent_marker_line_width,
            marker_symbol=population_possible_groups_markers[group],
            marker=population_color_dicts[group][state],
            text=template,
            hoverinfo='text'
        )

    
    def plot_current_locations(self):
        fig = go.Figure(
            layout=go.Layout(
                xaxis=dict(range=[self.xmin, self.xmax], autorange=False, zeroline=False),
                yaxis=dict(range=[self.ymin, self.ymax], autorange=False, zeroline=False),
                title_text="Current Population Locations",
                hovermode="closest"
            )
        )
        
        # Cycle runs along all agents in current population number
        for i in range(self.population_numbers[-1]):
            agent_dict = self.population[i].__dict__
            
            # Add traces
            fig.add_trace(
                self.go_agent_scatter(agent_dict)
            )
        
        fig.update_layout(showlegend=False)

        fig.show()
        

    def animate_population(self):        
        full_data = []
        
        t_list = list(set(agents.agents_info_df['step'].to_list()))
        
        for t in t_list:
            population_data = self.agents_info_df.loc[
                self.agents_info_df['step'] == t
            ].to_dict(orient='records')
            
            full_data.append([self.go_agent_scatter(population_data[i]) for i in range(len(population_data))])
        
        
        # Create figure
        fig = go.Figure(
            
            data=full_data[0],
            
            layout=go.Layout(
                width=600, 
                height=600,
                xaxis=dict(range=[self.xmin, self.xmax], autorange=False, zeroline=False),
                yaxis=dict(range=[self.ymin, self.ymax], autorange=False, zeroline=False),
                title="Moving Frenet Frame Along a Planar Curve",
                hovermode="closest",
                updatemenus=[
                    dict(
                        type="buttons",
                        buttons=[
                            dict(
                                label="Play",
                                method="animate",
                                args=[None]
                            )
                        ]
                    )
                ]
            ),
            frames=[go.Frame(data=full_data[t]) for t in t_list]
        )
        fig.update_layout(showlegend=False)

        fig.show()

In [0]:
population_group_list, population_state_list = initial_population_group_state_scene(
    population_number,
    vulnerable_number
)

agents = Population(
    population_number=population_number,
    vulnerable_number=vulnerable_number,
    population_group_list=population_group_list,
    population_state_list=population_state_list,
    horizontal_length=horizontal_length,
    vertical_length=vertical_length,
    maximum_speed=maximum_speed
)

In [70]:
agents.plot_current_locations()

In [0]:
for steps in range(60):
    agents.evolve_population()
#agents.plot_current_locations()

In [75]:
agents.animate_population()

Output hidden; open in https://colab.research.google.com to view.

In [76]:
plot_states_evolution_plotly(agents.agents_info_df)

## N=30

In [0]:
for steps in range(120):
    agents.evolve_population()
#agents.plot_current_locations()

In [42]:
agents.animate_population()

In [43]:
plot_states_evolution_plotly(agents.agents_info_df)

In [0]:
for steps in range(120):
    agents.evolve_population()
#agents.plot_current_locations()

In [34]:
agents.animate_population()

In [35]:
plot_states_evolution_plotly(agents.agents_info_df)

In [0]:
agents.evolve_population()
agents.plot_current_locations()

In [0]:
for steps in range(120):
    agents.evolve_population()
#agents.plot_current_locations()

In [25]:
agents.animate_population()

In [26]:
plot_states_evolution_plotly(agents.agents_info_df)

In [0]:
# Get number of steps in dataframe:
number_of_steps_dataframe_test = agents.agents_info_df.tail(1)['step'].to_numpy()[0]
days_array_test = np.arange(number_of_steps_dataframe_test+1)
# Tabla cruzada de estados y pasos (dias)
time_series_agents_test = pd.crosstab(agents.agents_info_df['state'], agents.agents_info_df['step']).fillna(0) * 100 / population_number # To get a percent of population
if len(time_series_agents_test.index) > 6:
    color_palette_test = color_palette_dead
elif len(time_series_agents_test.index) == 6:
    color_palette_test = color_palette_no_dead

In [196]:
time_series_agents_test.index

Index(['asymptomatic', 'dead', 'exposed', 'mildly-ill', 'recovered',
       'seriously-ill', 'susceptible'],
      dtype='object', name='state')

In [191]:
agents.agents_info_df

agent          x          y  ...  infected_by_agent  agent_can_spread_bool step
0        0  11.862559 -28.428858  ...               None                  False    0
1        1 -18.439300   5.941876  ...               None                  False    0
2        2  29.593131  -8.348968  ...               None                  False    0
3        3  10.086568  35.108935  ...               None                  False    0
4        4   3.458576   3.335158  ...               None                  False    0
...    ...        ...        ...  ...                ...                    ...  ...
7255    55 -25.244742   7.323790  ...                 35                  False  120
7256    56   6.529057 -12.275005  ...                 41                  False  120
7257    57 -17.353675   1.917088  ...                 25                   True  120
7258    58  12.443465  -6.750712  ...                 34                  False  120
7259    59 -32.078263 -25.844456  ...                 40                  False  120

[7260 rows x 16 columns]

In [0]:
examine_agent = 1
for i,j,k in zip(agents.agents_info_df[agents.agents_info_df['agent']==examine_agent]['agent_can_spread_bool'].to_numpy(),
                 agents.agents_info_df[agents.agents_info_df['agent']==examine_agent]['diagnosed'].to_numpy(), agents.agents_info_df[agents.agents_info_df['agent']==examine_agent]['state'].to_numpy()):
    print(i,j, k)

In [0]:
agents.agents_info_df[agents.agents_info_df['agent']==1]['state'].to_numpy()

In [0]:
agents.agents_info_df[agents.agents_info_df['step']==0]['probability_of_becoming_exposed']

In [0]:
[agents.population[i].probability_of_becoming_exposed for i in range(population_number)]

[0.21215295000479012,
 0.05438566202925606,
 1.0220980035764666,
 0.19450594337297467,
 0.04527789485605052,
 0.043745585067508225,
 0.16448011638358526,
 0.17436742740464628,
 0.625720459706267,
 0.1586963129699983,
 0.17546345422670864,
 0.7627743118469446,
 0.20270132832669185,
 0.181530618439968,
 0.6766638343039004,
 0.05100137551446414,
 0.17916158266979873,
 0.0470635861046238,
 0.038987811406447616,
 0.03458070186017967,
 0.15991691656924847,
 0.05392409159295754,
 0.2103485732689545,
 0.2022915296373132,
 0.643340643291222,
 0.14284693475067073,
 0.16789637733718704,
 0.18105124309793313,
 0.15469690601866717,
 0.19198168169670254]